# エンドツーエンドのコードファースト生成AIエクスペリメント

このノートブックでは、DataRobotが提供する生成AI機能の包括的な概要を説明します。

**Note**: For self-managed users, code samples that reference `app.datarobot.com` need to be changed to the appropriate URL for your instance.

In [ ]:
import datarobot as dr
from datarobot.models.genai.vector_database import VectorDatabase
from datarobot.models.genai.vector_database import ChunkingParameters
from datarobot.enums import PromptType
from datarobot.enums import VectorDatabaseEmbeddingModel
from datarobot.enums import VectorDatabaseChunkingMethod
from datarobot.models.genai.playground import Playground
from datarobot.models.genai.llm import LLMDefinition
from datarobot.models.genai.llm_blueprint import LLMBlueprint
from datarobot.models.genai.llm_blueprint import VectorDatabaseSettings
from datarobot.models.genai.chat import Chat
from datarobot.models.genai.chat_prompt import ChatPrompt
from datarobot.models.genai.vector_database import CustomModelVectorDatabaseValidation
from datarobot.models.genai.comparison_chat import ComparisonChat
from datarobot.models.genai.comparison_prompt import ComparisonPrompt
from datarobot.models.genai.custom_model_llm_validation import CustomModelLLMValidation

### DataRobotに接続する

[PythonクライアントからDataRobotに接続する](https://docs.datarobot.com/en/docs/api/api-quickstart/api-qs.html)ためのさまざまなオプションの詳細をご確認ください。

In [ ]:
endpoint="https://app.datarobot.com/api/v2"
token="<ADD_VALUE_HERE>"
dr.Client(endpoint=endpoint, token=token)

### ユースケースを作成

生成AIはDataRobotのユースケースの中で機能するので、新しいユースケースを作成することから始めます。

In [ ]:
use_case = dr.UseCase.create()

このワークフローでは、GenAIモデルでベクターデータベースを使用します。次に、一連のドキュメントを含むデータセットをアップロードします。

In [ ]:
# this can be updated with any public URL that is pointing to a .zip file
# in the expected format
dataset_url = "https://s3.amazonaws.com/datarobot_public_datasets/genai/pirate_resumes.zip"

# We will use a vector database with our GenAI models. Let's upload a dataset with our documents.
# If you wish to use a local file as dataset, change this to
# `dataset = dr.Dataset.create_from_file(local_file_path)`
dataset = dr.Dataset.create_from_url(dataset_url)

### ベクターデータベースの作成

In [ ]:
chunking_parameters = ChunkingParameters(
    embedding_model=VectorDatabaseEmbeddingModel.JINA_EMBEDDING_T_EN_V1,
    chunking_method=VectorDatabaseChunkingMethod.RECURSIVE,
    chunk_size=128,
    chunk_overlap_percentage=25,
    separators=[],
)
vdb = VectorDatabase.create(dataset.id, chunking_parameters, use_case)

以下のセルを使ってベクターデータベースを取得し、それが完了していることを確認します。
Approximate completion time is 30-60 seconds.

In [ ]:
vdb = VectorDatabase.get(vdb.id)
assert vdb.execution_status == "COMPLETED"

### LLMプレイグラウンドの作成

大規模言語モデル（LLM）をホストするLLMプレイグラウンドを作成します。

In [ ]:
playground = Playground.create(name="New playground for example", use_case=use_case)

以下のセルを使って、使用可能なLLMの種類を確認します。デフォルトでは、このメソッドは読みやすいようにdictとして返します。これには、各LLMで使用できる設定のリストと、値に対する制約が含まれます。

In [ ]:
llms_dict = LLMDefinition.list(use_case=use_case)
print(llms_dict)

例として、GPT 3.5を使用します。

In [ ]:
llms = LLMDefinition.list(use_case=use_case, as_dict=False)
gpt = llms[0]

GPTと対話するには、希望の設定でLLMブループリントを作成する必要があります。使用できる設定はLLMのタイプによって異なるため、ブループリントの作成時に検証される値を含む一般的なdictを取ります。GPTで使用できる設定を確認します。

In [ ]:
print([setting.to_dict() for setting in gpt.settings])

### LLMブループリントの作成

In [ ]:
llm_settings = {
    "system_prompt": (
        "You are a pirate who begins each response with 'Arrr' "
        "and ends each response with 'Matey!'"
    ),
    "max_completion_length": 256,  # Let's ask for short responses
    "temperature": 2.0,  # With a high degree of variability
}
# PromptType.ONE_TIME_PROMPT is an alternative if you don't wish
# for previous chat prompts (history) to be included in each subsequent prompt
prompting_strategy = PromptType.CHAT_HISTORY_AWARE

データベース作成時のデフォルトとは異なるベクターデータベース設定を使用します。

In [ ]:
vector_database_settings = VectorDatabaseSettings(
    max_documents_retrieved_per_prompt=2,
    max_tokens=128,
)

llm_blueprint = LLMBlueprint.create(
    playground=playground,
    name="GPT",
    llm=gpt,
    prompt_type=prompting_strategy,
    llm_settings=llm_settings,
    vector_database=vdb,
    vector_database_settings=vector_database_settings,
)

### Create a chat
Now create a chat and associate it with the LLM blueprint you just created.
A chat is the entity that groups together a set of prompt messages.
It can be thought of as a conversation with a particular LLM blueprint.

In [ ]:
chat = Chat.create(
    name="Resume review chat with a pirate",
    llm_blueprint=llm_blueprint
)

### LLMブループリントとのチャット

以下のセルを使って、LLMブループリントとチャットします。

In [ ]:
prompt1 = ChatPrompt.create(
    chat=chat,
    text="How can a pirate resume be evaluated?",
    wait_for_completion=True,
)
print(prompt1.result_text)

上のセル例は、`result_metadata`によって確認された、切り捨てられた出力を返します。

In [ ]:
print(prompt1.result_metadata.error_message)

`max_completion_length`を大きくして、もう一度チャットしてみます。LLM設定は、LLMブループリントがまだ保存されていない限り、チャットプロンプト内で更新できます。そうすることで、LLMブループリントの基本設定が更新されます。

In [ ]:
llm_settings["max_completion_length"] = 1024
prompt2 = ChatPrompt.create(
    text="Please answer the previous question again.",
    chat=chat,
    llm_settings=llm_settings,
    wait_for_completion=True,
)
print(prompt2.result_text)

新しい`max_completion_length`を維持して、LLMブループリントが更新されたことを確認できます。

In [ ]:
llm_blueprint = LLMBlueprint.get(llm_blueprint.id)
print(llm_blueprint.llm_settings)

回答が満足のいくものでないかもしれないため、次はTemperatureを下げて回答を修正します。

In [ ]:
llm_settings["temperature"] = 0.8
prompt3 = ChatPrompt.create(
    text="Please summarize the best pirate resume.",
    chat=chat,
    llm_settings=llm_settings,
    wait_for_completion=True,
)
print(prompt3.result_text)

LLMがベクターデータベースの情報を使用していることを確認します。

In [ ]:
print([citation.text for citation in prompt3.citations])

次に、既存のLLMブループリントから新しいLLMブループリントを作成し、いくつかの設定を変更して2つを比較します。

In [ ]:
new_llm_blueprint = LLMBlueprint.create_from_llm_blueprint(llm_blueprint, name="new blueprint")

新しいブループリントからベクターデータベースを削除し、以下のように設定を変更して、ブループリントを保存します。

In [ ]:
llm_settings["system_prompt"] = "You are an AI assistant who helps to evaluate resumes."
new_llm_blueprint = new_llm_blueprint.update(
    llm_settings=llm_settings,
    remove_vector_database=True,
)

Once you are satisfied with the blueprint, in the UI you can perform an [LLM blueprint comparison](https://docs.datarobot.com/en/docs/gen-ai/compare-llm.html) or [deploy it from the playground](https://docs.datarobot.com/en/docs/gen-ai/deploy-llm.html).


### Add a external vector database

Now add an external vector database from a deployment.
Note that creating the deployment is outside the scope of this example.
To continue with this portion of the example, first create an external vector database deployment, validate and deploy it, and update the `external_vdb_id` value here.

You can create an external vector database and deploy it by first following [this guide](https://docs.datarobot.com/en/docs/gen-ai/ext-vector-db.html)

Once you have done that, simply update your external vector database ID here to use it.

In [ ]:
external_vdb_id = "<ADD_VALUE_HERE>"

In [ ]:
# Now create a vector database
external_model_vdb = VectorDatabase.get(
    vector_database_id=external_vdb_id
)
assert external_model_vdb.execution_status == "COMPLETED"

### Add an external model LLM

Now add an external LLM blueprint from a deployment. Because creating the deployment is outside the scope of this example, it instead assumes a previously deployed text generation model.
To continue with this portion of the example, first create an external LLM deployment, validate it, and update the `external_llm_validation_id` value here.

You can create an external LLM and validate it by first following [this guide.](https://docs.datarobot.com/en/docs/gen-ai/ext-llm.html)

Once you have done that, update your external LLM validation ID here to use it.

In [ ]:
external_llm_validation_id = "<ADD_VALUE_HERE>"

In [ ]:
external_llm_validation = CustomModelLLMValidation.get(validation_id=external_llm_validation_id)
assert external_llm_validation.validation_status == "PASSED"

カスタムモデルLLMとカスタムモデルベクターデータベースを使ってLLMブループリントを作成できるようになりました。

In [ ]:
custom_model_llm_blueprint = LLMBlueprint.create(
    playground=playground,
    name="custom model LLM with custom model vdb",
    llm="custom-model",
    llm_settings={
        "validation_id": external_llm_validation.id,
        # NOTE - update this value based on the context size in tokens
        # of the external LLM that you are deploying
        "external_llm_context_size": 4096
    },
    vector_database=external_model_vdb,
)

### Create a comparison chat
Finally create a `comparison_chat` and associate it with a playground.
A comparison chat, analogous to the chat for a chat prompt, is the entity that groups together a set of comparison prompt messages.
It can be thought of as a conversation with one or more LLM blueprints.

In [ ]:
comparison_chat = ComparisonChat.create(
    name="Resume review comparison chat with a pirate",
    playground=playground
)

Now compare the LLM blueprints.
The response of the `custom_model_llm_blueprint` as it is setup in the documentation will not be related to the pirate resume and that is expected. Feel free to modify the external VDB creation and/or external LLM to suit your use case.

In [ ]:
comparison_prompt = ComparisonPrompt.create(
    llm_blueprints=[llm_blueprint, new_llm_blueprint, custom_model_llm_blueprint],
    text="Summarize the best resume",
    comparison_chat=comparison_chat,    
    wait_for_completion=True,
)
print([result.result_text for result in comparison_prompt.results])